In [1]:
#Razdel — сегментация текста на предложения и токены;
#Navec — качественный компактные эмбеддинги;
#Slovnet — современные компактные модели для морфологии, синтаксиса, NER;
#Yargy — правила и словари для извлечения структурированной информации;
#Ipymarkup — визуализация NER и синтаксической разметки;
!pip install natasha
!pip install natsort
!pip install navec

import os
import sys
import pickle
import re
from natsort import natsorted

import ipymarkup
from natasha import (
    Segmenter,
    MorphVocab,   
    NewsEmbedding,
    NewsMorphTagger,
    NewsSyntaxParser,
    NewsNERTagger, 
    PER,
    NamesExtractor,
    Doc
)

segmenter = Segmenter()
morph_vocab = MorphVocab()
emb = NewsEmbedding()
morph_tagger = NewsMorphTagger(emb)
syntax_parser = NewsSyntaxParser(emb)
ner_tagger = NewsNERTagger(emb)
names_extractor = NamesExtractor(morph_vocab)

In [2]:
def get_filepaths(d):
    # List which will store all of the full filepaths.
    locations = []
    # os.walk to get tree info
    for root, directories, files in os.walk(d):
        for filename in files:
            if filename.endswith(".pkl") and filename.startswith('ch'):
            # join the strings to form filepath
                filepath = os.path.join(root, filename)
                locations.append(filepath)
    # uses natsort to return human-intelligible ordering
    return natsorted(locations)

# store function results in a variable.   
sorted_filepaths = get_filepaths('/Users/Peter/Documents/GitHub/DSAM2019/')    

In [6]:
from ipymarkup.span import Span
from ipymarkup.dep import Dep
from ipymarkup.demo import show_table

from ipymarkup import (
    show_span_box_markup,
    show_span_ascii_markup,
    show_dep_markup
)
from ipymarkup.palette import palette, BLUE, ORANGE, PURPLE


wholebook = []
# for every filepath in list of filepaths
for f in sorted_filepaths:
    # open filepath as a string
    with open(str(f), 'rb') as f:
        data = pickle.load(f)
        # joins the list from the pickle file
        ch = ''.join(data)
        # appends list with joined chapter text
        wholebook.append(ch)
        f.close()
    
for f in wholebook:
    doc = Doc(f)
    # divides doc into tokens and sents, given start and stop properties
    doc.segment(segmenter)
    # every token is morphologically tagged, given pos and feats properties
    doc.tag_morph(morph_tagger)
    # named entity recognition
    doc.tag_ner(ner_tagger)
    # extract names from PER span type
    for span in doc.spans:
        if span.type == PER:
            span.normalize(morph_vocab)
            span.extract_fact(names_extractor)
    
    #doc.sents[0].morph.print()
    print(doc.tokens[0])
    #doc.sents.ner.print()
    #print(doc.sents[0])
    print(doc.spans[0])
    print("\n")


DocToken(stop=6, text='Москва', pos='PROPN', feats=<Inan,Nom,Fem,Sing>)
DocSpan(stop=6, type='LOC', text='Москва', tokens=[...])


DocToken(stop=1, text='В', pos='ADP')
DocSpan(start=203, stop=221, type='PER', text='Иудеи Понтий Пилат', tokens=[...], normal='Иудея Понтий Пилат', fact=DocFact(slots=[...]))


DocToken(stop=1, text='–', pos='PUNCT')
DocSpan(start=46, stop=61, type='PER', text='Иван Николаевич', tokens=[...], normal='Иван Николаевич', fact=DocFact(slots=[...]))


DocToken(stop=6, text='Утихли', pos='VERB', feats=<Perf,Ind,Plur,Past,Fin,Mid>)
DocSpan(start=280, stop=295, type='PER', text='Иван Николаевич', tokens=[...], normal='Иван Николаевич', fact=DocFact(slots=[...]))


DocToken(stop=9, text='Старинный', pos='ADJ', feats=<Nom,Pos,Masc,Sing>)
DocSpan(start=459, stop=491, type='PER', text='Александра Сергеевича Грибоедова', tokens=[...], normal='Александр Сергеевич Грибоедов', fact=DocFact(slots=[...]))


DocToken(stop=5, text='Когда', pos='SCONJ')
DocSpan(start=76, stop=

In [ ]:
for f in wholebook:
    doc = Doc(f)   
    doc.segment(segmenter)
    doc.tag_morph(morph_tagger)
    # lemmatizer
    #for token in doc.tokens:
    #    token.lemmatize(morph_vocab)
    # parse syntax
    doc.parse_syntax(syntax_parser)
    #print(doc.tokens[0])
    #print(doc.sents[0])
    doc.sents[0].syntax.print()
    
    #markup = syntax_parser(doc.sents[0].syntax)
    #markup.print()
    #print("\n")
    

          ┌──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────► Москва             nsubj
          │                                                                                                                                                                                                                                                                                                    1984               
          │                                                 ┌────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────► Текст              obj
          │            

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



                                                                                                                                                                                                                                                                                                                                                                ┌──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────► –              punct
                ┌──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────────►│                                                                                                 

                                                                                                                                                 Утихли         
                                                                                                                                        ┌──────► истерические   amod
                                                                                                                                        │     ┌► женские        amod
                                                                                                                            ┌──────────►│   ┌─└─ крики          nsubj
                                                                                                              ┌────────────►│           │   │    отсверлили     conj
                                                                                                              │             │           │ ┌►│ ┌─ свистки        amod
             

                                                      ┌──► Старинный          amod
                                                      │ ┌► двухэтажный        amod
                ┌─────┌────────────────────────────►┌─└─└─ дом                nsubj
                │     │                             │   ┌► кремового          amod
                │     │                             └──►└─ цвета              nmod
        ┌───────│   ┌─│                         ┌─┌─┌───── помещался          
        │       │   │ │                         │ │ │ ┌──► на                 case
        │       │   │ │                         │ │ │ │ ┌► бульварном         amod
        │       │   │ │                         │ │ └►└─└─ кольце             obl
        │       │   │ │                         │ │     ┌► в                  case
        │       │   │ │                         │ └────►└─ глубине            obl
        │       │   │ │                         │       ┌► чахлого            amod
        │

...

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      ┌────────────────────────────────────────────────────────────────────────────────────────────────────────────► Бор                   nsubj
                                                                                                                                                                                                                                                                                                                                                                                                       

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      ┌► Маленький          amod
┌──────────────────────────────────────────────────────────────────────────────────────────────────────────────────────

                                                                                                                                      ┌──────────► Итак            advmod
                                                                                                                                      │         ┌► неизвестный     nsubj
      ┌───────────────────────────────────────────────────────────────────────┌─────────────────────────────────┌─────────────────────│       ┌─└─ погрозил        
      │                                                                       │                                 │                     │       └──► Ивану           appos
      │                                                                       │                                 │                     │ ┌────────► пальцем         advmod
      │                                                                       │                                 │                     │ │       ┌► и          

                                                                                                                                                                                                                                                                                                                                                                                      ┌► Не              advmod
┌───┌─┌─────┌───────────┌───┌─┌───────┌───────┌───────────────────────────────────────────────────────────────┌─────────────────────┌───────────────────────────────────────────────────────────────────────────────┌─────┌─────────┌─────────────┌─┌───────┌─────────┌───────────────────────────────────────────────────────────┌───────────────────┌─────────────────┌─┌─┌─┌───┌─┌─└─ выдержали       
│   │ │     │           │   │ │       │       │                                                               │                     │                                                                         

                                                                                                                             Нетрудно       
                      ┌────────────────────────────────────────────────────────────────────────────────────────────────────► догадаться     xcomp
  ┌──────────────────►│                                                                                                      что            obj
  │                   │           ┌──────────────────────►┌───────────────────────────────────────────────────────────────── толстяк        nsubj
  │                   │           │                       │                                                       ┌────────► с              case
  │                   │         ┌►│                       │                                                       │          багровой       amod
  │                   │         │ │                       │                                                       │     ┌►┌─ физионом